
  <head>
    <meta http-equiv="Content-Type" content="text/html; charset=utf-8" />
    <meta http-equiv="Content-Style-Type" content="text/css" />
    <meta name="generator" content="pandoc" />
    <title></title>
    <style type="text/css">code{white-space: pre;}</style>
  </head>
  



<h1> AMI </h1> 
<h1> Procesamiento de audio mediante clasificadores </h1>

<br>
    
En este notebook veremos como emplear clasificadores para procesamiento de audio. Concretamente, mostraremos como detectar el género musical al que pertenece una canción (ROCK/POP/CLASICA/...). Para ello partimos de un dataset con canciones donde se conoce el genero de cada una de ellas. A partir del dataset construiremos el matrix de features X, extrayendo para cada canción las medias y varianzas de los coeficientes cepstrales de Mel (MFCC). MFCC es un tipo de transformación que se emplea habitualmente en procesamiento de audio y se sabe adecuada para la identificación de contenido relevante (genero musical, identificación de un hablante, etc.). 

Puede consultarse <a href="https://www.wikiwand.com/es/MFCC"> la entrada de la wikipedia</a> para información más detallada.  

<h2> Obtención de los MFCC en Python </h2>

Empezaremos calculando las features asociadas a un fichero de audio. 

Existen diversas implementaciones disponibles de este procedimiento en Python. Nosotros emplearemos el método descrito en <a src="http://haythamfayek.com/2016/04/21/speech-processing-for-machine-learning.html"> en este enlace </a>. Puede consultarse también <a src="http://www.practicalcryptography.com/miscellaneous/machine-learning/guide-mel-frequency-cepstral-coefficients-mfccs/"> este documento </a> para una explicación más precisa del procedimiento involucrado. 

Los fuentes de la librería anterior están disponibles en el directorio github: 

<a href="https://github.com/jameslyons/python_speech_features"> https://github.com/jameslyons/python_speech_features </a>

Desde el notebook puede instalar este paquete (y otros adicionales que usaremos después) mediante los comandos:

In [ ]:
# Instalación de las librerias
# Este no es el método más "limpio", pero es el que nos permite realizar la instalación como usuarios via "sudo"
!sudo pip3 install --upgrade pip
!sudo apt-get -y install libportaudio0 libportaudio2 libportaudiocpp0 portaudio19-dev
!sudo pip3 install python_speech_features pydub pyaudio

A continuación descargaremos y descomprimiremos un fichero con wavs de ejemplo que usaremos durante este sesión: 

In [ ]:
import os.path
from urllib.request import urlretrieve
import tarfile

url = 'http://jval.es/wavs.tar.gz'
full_path = os.path.join('', 'wavs.tar.gz')
print('Descargando fichero en: ' + full_path)
urlretrieve(url, full_path)

tf = tarfile.open(full_path)
wav_names = [fname for fname in tf.getnames() if ".wav" or ".mp3" in fname.split(os.sep)[-1]]
wav_names = [fname for fname in wav_names if "._" not in fname.split(os.sep)[-1]]

for wav_name in wav_names:
    print('Extrayendo ' + wav_name)
    tf.extract(wav_name)

Podemos usar la siguiente función de python para crear en HTML un control para reproducir un fichero de audio:

In [ ]:
def audioPlayer(filepath, tipo='wav'):
    """ will display html 5 player for compatible browser

    Parameters :
    ------------
    filepath : relative filepath with respect to the notebook directory ( where the .ipynb are not cwd)
               of the file to play

    The browser need to know how to play wav through html5.

    there is no autoplay to prevent file playing when the browser opens
    """
    
    src = """
    <head>
    <meta http-equiv="Content-Type" content="text/html; charset=utf-8">
    <title>Simple Test</title>
    </head>
    
    <body>
    <audio controls="controls" preload="none" style="width:600px" >
      <source src="files/%s" type="audio/%s" />
      Your browser does not support the audio element.
    </audio>
    </body>
    """%(filepath, tipo)
    display(HTML(src))   

Vamos a escuchar los ficheros llamando a la función anterior:

In [ ]:
audioPlayer('drums.wav')

In [ ]:
audioPlayer('drums.mp3')

Si su navegador no reproduce el sonido, puede descargar el fichero a la máquina local pulsando con el botón derecho del ratón y seleccionando la opción de guardar fichero. Pruebe a guardar el mp3 anterior en su máquina.

<h3> Cálculo de las características </h3>

Ahora, para calcular los MFCC crearemos la función <b>getFeatures</b>, que reciba como argumento el nombre del fichero a analizar, y que devuelve las medias y las varianzas de los coeficientes. Esta función posee las siguientes características:

<ul>
    <li> La función recibe como argumento cualquier fichero de audio (wav, mp3, ogg, etc)
    <li> Independientemente de la longitud del audio, al calcular las medias y varianza la salida posee un tamaño constante. Este tamaño depende de la configuración que se elija al calcular los MFCC. En nuestro caso será un vector de 52 posiciones (26 de medias y 26 de desviaciones típicas) 
    <li> La ejecución del cálculo de los MFCC es lenta (operaciones pesadas computacionalmente). Para reducir el tiempo de ejecución se procesarán a lo sumo MAX segundos escogidos en el medio del fichero 
</ul>

In [ ]:
# Ejemplo de calculo de las features de un .wav

from python_speech_features import mfcc
from python_speech_features import delta
from python_speech_features import logfbank
from pydub import AudioSegment
import numpy as np
import array
from pydub.utils import get_array_type

# La función recibe como argumento el nombre de un fichero de audio, coge un máximo de MAX segundos de duración
def getFeatures(fichero, MAX=5):
    file = AudioSegment.from_file(fichero)
    rate = file.frame_rate
    bit_depth = file.sample_width * 8
    array_type = get_array_type(bit_depth)
    sig = np.array(array.array(array_type, file._data))
    base = 2048;
    length = int(np.floor(rate*MAX*1.0 / base) * base)
    medio = int(len(sig)/2)
    sigmin = int(medio-length/2)
    sigmax = int(medio+length/2) 
    sig = sig[sigmin:sigmax:]
    mfcc_feat = mfcc(sig,samplerate=rate,nfft=base)
    d_mfcc_feat = delta(mfcc_feat, 2)
    feat = logfbank(sig,samplerate=rate,nfft=base)
    mean = feat.mean(axis=0)
    std = feat.std(axis=0)
    x = np.concatenate((mean, std), axis=0) # Features del wav
    return x

# Para probarlo descargar los ficheros wav de muestra al directorio de trabajo del notebook
%time x = getFeatures('english.wav',MAX=5)
print(x, x.shape)

# Este fichero es mucho mas largo, pero el tamaño del vector de características no cambia
# El tiempo aumentan por manejar arrays de longitud mucho mayor
%time x = getFeatures('drums.wav',MAX=5)
print(x, x.shape)
 
# La función también soporta ficheros mp3, ogg, etc. Puede observar que el resultado es identico
# El tiempo de procesado es mucho mayor al tener que decodificar el mp3
%time x = getFeatures('drums.mp3',MAX=5)
print(x, x.shape)

<h2> Construcción del dataset </h2>

El objetivo ahora es crear un clasificador que diferencie entre varios tipos de generos musicales. Para ello debemos crear un dataset del tipo [X, y] al igual que los que hemos empleado en clases anteriores. Se suministra para ello el fichero de ejemplo dataset.tar.gz, que contiene los siguientes directorios: 

<ol>
    <li> CLASICA, 34 canciones de música clásica
    <li> ROCK, 34 canciones de música rock
    <li> TEST, 12 canciones <b>no</b> incluidas en los directorios anteriores, 6 de tipo clasica y 6 de tipo rock
</ol>

El dataset en este caso se facilita en mp3 dado el gran volumen que ocuparía en wav. Puede descargarlas mediante el comando siguiente: (tamaño necesario ~1.4 Gb, la operación tarda unos 3-5 minutos)

In [ ]:
import os.path
from urllib.request import urlretrieve
import tarfile

url = 'http://jval.es/dataset.tar.gz'
full_path = os.path.join('', 'dataset.tar.gz')
print('Descargando fichero en: ' + full_path)
urlretrieve(url, full_path)

tf = tarfile.open(full_path)
mp3_names = [fname for fname in tf.getnames() if ".mp3" in fname.split(os.sep)[-1]]
mp3_names = [fname for fname in mp3_names if "._" not in fname.split(os.sep)[-1]]

for mp3_name in mp3_names:
    print('Extrayendo ' + mp3_name)
    tf.extract(mp3_name)
 
# Borramos el dataset comprimido para ahorrar espacio
os.remove(full_path)

Una vez disponible el dataset, vamos a procesar ambos directorios para construir las matrices X, y correspondientes a este problema de aprendizaje. Para ello emplearemos el siguiente código. Fíjese que sería muy sencillo extenderlo a más de dos clases (seleccionando valores adecuados en el vector y).

In [ ]:
# GENERA MODELO X,y PARA DOS CLASES: CLASICA Y ROCK
import os.path
from sklearn import svm
from sklearn import datasets
from sklearn.externals import joblib
from sklearn.datasets import fetch_mldata
from sklearn.linear_model import SGDClassifier

def procesaDir(path):
    # Devuelve matriz de features X y numero de canciones de este tipo
    X = np.empty(shape=[0,52])
    contador = 0
    for x in os.listdir(path):
        (nombre, ext) = os.path.splitext(x)
        if os.path.isfile(os.path.join(path, x)) and (ext== ".mp3"):
            contador+=1
            file = path+nombre+ext
            print('Procesando ' + file);
            # FALTA, DEBE IR GENERANDO LA MATRIZ X
    return X, contador
            
X1, num1 = procesaDir('CLASICA/')
y1 = # FALTA, DEBE FORMAR EL VECTOR y1
X2, num2 = procesaDir('ROCK/')
y2 = # FALTA, DEBE FORMAR EL VECTOR y2
    
# Creamos el dataset global
X = np.r_[X1,X2]
y = np.r_[y1,y2]

<h3> Entrenamiento </h3>

A continuación entrenará el clasificador empleando los métodos estudiados en la práctica anterior (se recomienda usar directamente el clasificador de scikitlearn). Se muestra el código de un clasificador logístico con sci-kit learn, y donde guardamos el modelo a fichero para su uso posterior, ya que no es necesario realizar reentrenamientos. 

In [ ]:
# Puede probar otros modelos de clasificadores, p.ej. los documentados en el libro de referencia disponible en aula virtual

clf = SGDClassifier(random_state=1, tol=0.001);
clf.fit(X, y.reshape(y.shape[0],));
joblib.dump(clf, 'clasicavsrock.pkl') 

<h3> Predicción </h3> 

Podemos ahora realizar predicciones sobre nuevos audios:

In [ ]:
# Si no esta cargado el modelo lo leemos del disco
if 'clf' not in globals():
    clf = joblib.load('clasicavsrock.pkl')

def testDir(path):
    contador = 0
    contadorROCK = 0
    contadorCLASICA = 0
    for x in os.listdir(path):
        (nombre, ext) = os.path.splitext(x)
        if os.path.isfile(os.path.join(path, x)) and (ext== ".mp3"):
            contador+=1
            file = path+nombre+ext
            print('Prediciendo ' + file);
            x = # FALTA, DEBE OBTENER LAS CARACTERISTICAS DE ESTE AUDIO
            result = clf.predict([x]);
            if result==0:
                print('CLASICA')
                contadorCLASICA += 1
            else:
                print('ROCK')
                contadorROCK += 1

    return contador, contadorCLASICA, contadorROCK

testDir('TEST/')

<h2> Clasificación de sonido en tiempo real </h2>

Una vez entrenada la red la usaremos para clasificar el sonido ambiente (usando como fuente de entrada el micrófono). Para ello, recordemos que puede emplear la librería pyaudio con el siguiente código para obtener una grabación: 

In [ ]:
import pyaudio
import numpy as np
import wave
import matplotlib.pyplot as plt
import scipy.constants as const
import scipy
from scipy.io import wavfile
from IPython.core.display import HTML

def getWav(tiempo=5, filename='test.wav'):
 
    try:
        CHUNK = 1024  # Habitualmente se encuentra con un valor de 1024
        FORMAT = pyaudio.paInt16
        CHANNELS = 1  # 1, mono    2, stereo
        RATE = 32000  # Valor obtenido de RATE en el código anterior
        RECORD_SECONDS = tiempo  # tiempo de captura, a determinar
        WAVE_OUTPUT_FILENAME = filename
        INPUT_DEVICE_INDEX = 2
        
        p = pyaudio.PyAudio()
        info = p.get_host_api_info_by_index(0)
        numdevices = info.get('deviceCount')
        for i in range(0, numdevices):
            if (p.get_device_info_by_host_api_device_index(0, i).get('maxInputChannels')) > 0:
                INPUT_DEVICE_INDEX = i       
                dev = p.get_device_info_by_host_api_device_index(0, i)
                print("Input Device id ", i, " - ", dev.get('name'))
                break
        
        stream = p.open(format=FORMAT,
                        channels=CHANNELS, 
                        rate=RATE, 
                        input=True,
                        input_device_index = INPUT_DEVICE_INDEX,
                        frames_per_buffer=CHUNK)

        print("Grabando ....")

        frames = []

        for i in range(0, int(RATE / CHUNK * RECORD_SECONDS)):
        #    print(i)
            data = stream.read(CHUNK)
            frames.append(data)

        print("Grabación finalizada.")

        stream.stop_stream()
        stream.close()
        p.terminate()

        wf = wave.open(WAVE_OUTPUT_FILENAME, 'wb')
        wf.setnchannels(CHANNELS)
        wf.setsampwidth(p.get_sample_size(FORMAT))
        wf.setframerate(RATE)
        wf.writeframes(b''.join(frames))
        wf.close()
    
    except (ValueError, PermissionError):
        print ("ERROR: Algo ha ido mal.")
        return False

    return True
          
file='test.wav'
getWav(filename=file, tiempo=5)

#Extract Raw Audio from Wav File
with wave.open(file,'r') as wav_file:
    #Extract Raw Audio from Wav File
    signal = wav_file.readframes(-1)
    signal = np.frombuffer(signal, dtype=np.int16)

    #Split the data into channels 
    channels = [[] for channel in range(wav_file.getnchannels())]
    for index, datum in enumerate(signal):
        channels[index%len(channels)].append(datum)

    #Get time from indices
    fs = wav_file.getframerate()
    Time=np.linspace(0, len(signal)/len(channels)/fs, num=len(signal)//len(channels))

    #Plot
    plt.figure(1)
    plt.title('Signal Wave...')
    for channel in channels:
        plt.plot(Time,channel)
    plt.show()
    
    
audioPlayer('test.wav')

<h2> Tarea </h2>

Escriba un código en python que esté permanentemente a la escucha grabando sonido durante unos segundos, analizando el tipo de canciones y mostrando la predicción por pantalla. 